# Chapter 1 - EIA API - Python Client

In this section, we will see how query the EIA API with Python using. We will use the eia_api.py to send GET requests to the API.

We will continue with the same example we used before - the hourly demand of electricity for balancing authority subregion PGAE. As before, we will use the API dashboard to extract the GET request:

<figure>
<img src="./images/query-detail.png" width="100%" align="center"/></a>
<figcaption> Figure 1 - The GET request details for balancing authority subregion PGAE</figcaption>
</figure>

The `eia_api.py` file provides a set of functions to query data from the EIA API V2. This includes the following functions:

- `eia_get` - to send GET request for data
- `eia_metadata` - to send GET request for metadata
- `eia_backfill` - to send a GET request for large data (more than 5000 observations)

In [1]:
import eia_api as api

In addition, we will import the following libraries:

In [2]:
import os
import datetime
import plotly.express as px

## Pulling Metadata

Setting the api key and the api path to pull data:

In [3]:
api_key = os.getenv('EIA_API_KEY')

api_meta_path = "electricity/rto/region-sub-ba-data/"

Sending GET request for route metadata:

In [4]:
meta = api.eia_metadata(
    api_key = api_key,
    api_path = api_meta_path  
)

In [5]:
meta.meta

{'id': 'region-sub-ba-data',
 'name': 'Hourly Demand by Subregion',
 'description': 'Hourly demand by balancing authority subregion.  \n    Source: Form EIA-930\n    Product: Hourly Electric Grid Monitor',
 'frequency': [{'id': 'hourly',
   'alias': 'hourly (UTC)',
   'description': 'One data point for each hour in UTC time.',
   'query': 'H',
   'format': 'YYYY-MM-DD"T"HH24'},
  {'id': 'local-hourly',
   'alias': 'hourly (Local Time Zone)',
   'description': 'One data point for each hour in local time.',
   'query': 'LH',
   'format': 'YYYY-MM-DD"T"HH24TZH'}],
 'facets': [{'id': 'subba', 'description': 'Subregion'},
  {'id': 'parent', 'description': 'Balancing Authority'}],
 'data': {'value': {'aggregation-method': 'SUM',
   'alias': 'Demand',
   'units': 'megawatthours'}},
 'startPeriod': '2018-06-19T05',
 'endPeriod': '2024-02-27T08',
 'defaultDateFormat': 'YYYY-MM-DD"T"HH24',
 'defaultFrequency': 'hourly'}

## Sending A Simple GET Request

Setting a GET Request:

In [6]:
api_key = os.getenv('EIA_API_KEY')

api_path = "electricity/rto/region-sub-ba-data/data/"

frequency = "hourly"

facets = {
    "parent": "CISO",
    "subba": "PGAE"
}

In [7]:
df1 = api.eia_get(
    api_key = api_key,
    api_path = api_path,
    frequency = frequency,
    facets = facets
)

In [8]:
df1.url

'https://api.eia.gov/v2/electricity/rto/region-sub-ba-data/data/?data[]=value&facets[parent][]=CISO&facets[subba][]=PGAE&frequency=hourly&api_key='

In [9]:
df1.parameters

{'api_path': 'electricity/rto/region-sub-ba-data/data/',
 'data': 'value',
 'facets': {'parent': 'CISO', 'subba': 'PGAE'},
 'start': None,
 'end': None,
 'length': None,
 'offset': None,
 'frequency': 'hourly'}

In [10]:
df1.data

period subba                subba-name parent  \
1545 2018-11-04 22:00:00  PGAE  Pacific Gas and Electric   CISO   
1568 2018-11-04 23:00:00  PGAE  Pacific Gas and Electric   CISO   
3632 2018-11-05 03:00:00  PGAE  Pacific Gas and Electric   CISO   
1554 2018-11-05 05:00:00  PGAE  Pacific Gas and Electric   CISO   
1863 2018-11-16 21:00:00  PGAE  Pacific Gas and Electric   CISO   
...                  ...   ...                       ...    ...   
4426 2024-02-25 04:00:00  PGAE  Pacific Gas and Electric   CISO   
4419 2024-02-25 05:00:00  PGAE  Pacific Gas and Electric   CISO   
4421 2024-02-25 06:00:00  PGAE  Pacific Gas and Electric   CISO   
4461 2024-02-25 07:00:00  PGAE  Pacific Gas and Electric   CISO   
4447 2024-02-25 08:00:00  PGAE  Pacific Gas and Electric   CISO   

                                 parent-name  value    value-units  
1545  California Independent System Operator  10112  megawatthours  
1568  California Independent System Operator  10209  megawatthours  
3632  California Independent System Operator  12183  megawatthours  
1554  California Independent System Operator  11410  megawatthours  
1863  California Independent System Operator  11061  megawatthours  
...                                      ...    ...            ...  
4426  California Independent System Operator  10789  megawatthours  
4419  California Independent System Operator  10648  megawatthours  
4421  California Independent System Operator  10452  megawatthours  
4461  California Independent System Operator  10183  megawatthours  
4447  California Independent System Operator   9810  megawatthours  

[5000 rows x 7 columns]

In [11]:
df1.data.dtypes

period         datetime64[ns]
subba                  object
subba-name             object
parent                 object
parent-name            object
value                   int64
value-units            object
dtype: object

## API Limitation

Let's plot the series:

In [19]:

px.line(df1.data, x= "period", y= "value")


The `start` and `end` arguments enable us to set a time range to the GET request. For example, let's pull data betweem January 1st, 2024 and February 24th, 2024:

In [20]:
start = datetime.datetime(2024, 1, 1, 1)
end = datetime.datetime(2024, 2, 24, 23)

df2 = api.eia_get(
    api_key = api_key,
    api_path = api_path,
    frequency = frequency,
    facets = facets,
    start = start,
    end = end
)

In [21]:
px.line(df2.data, x="period", y="value")

## Handling A Large Data Request

When we have to pull a series with a number of observations that exceed the API limitation of 5000 observations per call, use the `eia_backfill` function. The function splits the request into multiple small requests, where the `offset` argument defines the size of each request. It is recommended not to use an offset larger than 2500 observations. For example, let's pull data since July 1st, 2018:

In [22]:
start = datetime.datetime(2018, 7, 1, 8)
end = datetime.datetime(2024, 2, 24, 23)
offset = 2250

df3 = api.eia_backfill(
  start = start,
  end = end,
  offset = offset,
  api_path= api_path,
  api_key = api_key,
  facets = facets)

In [23]:
df3.data



period subba                subba-name parent  \
1619 2018-07-01 08:00:00  PGAE  Pacific Gas and Electric   CISO   
1620 2018-07-01 09:00:00  PGAE  Pacific Gas and Electric   CISO   
1621 2018-07-01 10:00:00  PGAE  Pacific Gas and Electric   CISO   
1622 2018-07-01 11:00:00  PGAE  Pacific Gas and Electric   CISO   
1623 2018-07-01 12:00:00  PGAE  Pacific Gas and Electric   CISO   
...                  ...   ...                       ...    ...   
40   2024-02-24 19:00:00  PGAE  Pacific Gas and Electric   CISO   
37   2024-02-24 20:00:00  PGAE  Pacific Gas and Electric   CISO   
35   2024-02-24 21:00:00  PGAE  Pacific Gas and Electric   CISO   
42   2024-02-24 22:00:00  PGAE  Pacific Gas and Electric   CISO   
33   2024-02-24 23:00:00  PGAE  Pacific Gas and Electric   CISO   

                                 parent-name  value    value-units  
1619  California Independent System Operator  12522  megawatthours  
1620  California Independent System Operator  11745  megawatthours  
1621  California Independent System Operator  11200  megawatthours  
1622  California Independent System Operator  10822  megawatthours  
1623  California Independent System Operator  10644  megawatthours  
...                                      ...    ...            ...  
40    California Independent System Operator   8252  megawatthours  
37    California Independent System Operator   7508  megawatthours  
35    California Independent System Operator   6670  megawatthours  
42    California Independent System Operator   6514  megawatthours  
33    California Independent System Operator   6620  megawatthours  

[49454 rows x 7 columns]

In [24]:
p = px.line(df3.data, x="period", y="value")
p.show()